# Scraping Sherdog

I wrote this code to scrape Sherdog for MMA fighters. The way the code works, I make a tree. I start with one fighter, and I use him to get the links of his opponents. I then scrape his opponents' pages for the fighters they fought. The code continues to do this until every page it can link to is scraped. 
1. This may not get everyone, if there are two fighters A and B that never fought anyone else, then I could only scrape their pages if I picked one to begin with.
2. I start with Daniel Cormier, a 2-time UFC Champion for the light heavyweight and heavyweight divisions, because he fought many people and fought in two weight classes. 
3. I do this in two steps, (1) I use a function make_tree to find all the fighters that I can get and (2) I use another function to go to the pages found and scrape the data.
4. I wrote a loop over the first function to append the webpages to a list without replacement. This avoids a never-ending loop in which I continue to go to Daniel's webpage, or anyone else's, whenever someone fought him. 

In [16]:
from bs4 import BeautifulSoup as sp
import requests
import pandas as pd 
import os
from numpy import loadtxt

In [1]:
path = "C:/Users/Juan/Dropbox/mma/"
raw = path + "rawdata/sherdog/"

### File Name
I want to store the data, so I used this next piece to ensure that I would make file names in the correct, existing directory.

In [ ]:
link = "/dgsg/Daniel-Cormier-52311"

if link.startswith("/fighter/"): #need this to add the entry to sherdog list of all links scraped
    file_name = link[9:]
else :
    file_name = link.replace("/","_")

print(file_name)

## make_tree(link)
This is the fist code, make_tree(link), that goes to a webpage(link) and gets all the opponent_links available.
*I have an exception to ensure the webpage can be reached* 

In [ ]:
def make_tree(link):
    url = "https://www.sherdog.com" + link
    
    try :
        page = requests.get(url, headers={"User-agent":"Mozilla/5.0"})
        
        fighter = sp(page.text,"html.parser")

        tables = fighter.find_all("table")

        rows = tables[1].find_all("tr")
    except :
        page = "bad link"
        #print(f'{err}')
    
    if page!="bad link":
        all_opponent_links = []
        all_fights = []
        for i in range(1,len(rows)):
            fight = rows[i].find_all("td")

            opponent_link = fight[1].find_all('a',href=True)[0].get("href")

            all_opponent_links.append(opponent_link)

        #for opponents in all_opponent_links:
        return all_opponent_links
    else :
        print("%s is a bad link" %(link))
        all_opponent_links = []
        return all_opponent_links

### Making big_list
I create an empty list, add Daniel, then let the code begin. It stops when there are no fighters left. 

In [ ]:
big_list = []
big_list.append("/fighter/Daniel-Cormier-52311")
over = 0
while over <1:
    for i in big_list:
        added = 0
        for j in make_tree(i):
            if j not in big_list:
                big_list.append(j)
                added +=1
        print(len(big_list))
        print(i)
    if added == 0:
        over = 1

In [ ]:
print(len(big_list))

### I store and save all the links for future reference 

In [ ]:
with open(path+'sherdog_big_list.txt', 'w') as f:
    for line in big_list:
        f.write(line)
        f.write('\n')
    f.close()

## make_data(link)
This is the function to extract the data for each fighter. For each fight of a fighter's professional career, it collects the opponent, event, date, result, method, round, time, and referee. 

In [3]:
def make_data(link):
    url = "https://www.sherdog.com" + link
    
    try :
        page = requests.get(url, headers={"User-agent":"Mozilla/5.0"})
    except :
        page = "bad link"
        #print(f'{err}')
    
    if page!="bad link":
        fighter = sp(page.text,"html.parser")

        tables = fighter.find_all("table")

        rows = tables[1].find_all("tr")

        all_fights = []
        for i in range(1,len(rows)):
            fight = rows[i].find_all("td")

            result = fight[0].text

            opponent_link = fight[1].find_all('a',href=True)[0].get("href")

            event = fight[2].find_all('a',href=True)
            event_link = event[0].get("href")
            event_string = event[0].text
            
            raw_date = fight[2].find_all("span",class_='sub_line')
            date = raw_date[0].text
            
            raw_method = fight[3].find_all("b")
            method = raw_method[0].text

            raw_referee = fight[3].find_all("span")
            referee = raw_referee[0].text

            rounds = fight[4].text
            time = fight[5].text

            clean_entry = [result,opponent_link,event_link,event_string,date,method,referee,rounds,time]
            all_fights.append(clean_entry)

            if link.startswith("/fighter/"): 
                file_name = link[9:]
            else :
                file_name = link.replace("/","_")

        #print(all_fights)
        df = pd.DataFrame(all_fights)
        df.columns = ["result","opponent_link","event_link","event_string","date","method","referee","rounds","time"]
        df.to_csv(raw+file_name+".txt", index=False)

    else :
        print("%s is a bad link" %(link))

### I import the text file 

In [4]:
#read text file into list
data = loadtxt(path+'sherdog_big_list.txt',dtype='str')

In [11]:
print(data)
print(len(data))

['/fighter/Daniel-Cormier-52311,' '/fighter/Stipe-Miocic-39537,'
 '/fighter/Derrick-Lewis-59284,' ... '/fighter/Dekazu-Dekazu-88307,'
 '/fighter/Takumi-Suzuki-88283,' '/fighter/Yoshihiro-Ito-88305,']
122181


I make a new list, it's exactly the same as big_list, with the links for the webpages that I will scrape. 

In [6]:
new_list = []
for i in data:
    text = i.replace(",","")
    new_list.append(text)
print(new_list[44])

/fighter/Curtis-Blaydes-172939


### Scraping
For every link in new_list, I try to scrape the relevant data. 
*I wrote in an exception, just in case, and store all failed links to a list. 

In [ ]:
didnt_work = []
for i in new_list:
    try : 
        make_data(i)
        print("Made data for %s" %(i))
    except :
        didnt_work.append(i)
        print("Can't make the data for %s" %(i)) 

Code got stuck after Dore Timar. Not sure why, but will simply begin from Dore to finish the loop.

In [10]:
for i in range(0,len(new_list)):
    if new_list[i] == "/fighter/Dora-Timar-368982":
        print(i)
    else :
        continue 

121876


In [14]:
didnt_work_pt2 = []
for i in range(121876,len(new_list)):
    try : 
        make_data(new_list[i])
        print("Made data for %s" %(i))
    except :
        didnt_work_pt2.append(new_list[i])
        print("Can't make the data for %s" %(i)) 

Made data for 121876
Made data for 121877
Made data for 121878
Made data for 121879
Made data for 121880
Made data for 121881
Made data for 121882
Made data for 121883
Made data for 121884
Made data for 121885
Made data for 121886
Made data for 121887
Made data for 121888
Made data for 121889
Made data for 121890
Made data for 121891
Made data for 121892
Made data for 121893
Made data for 121894
Made data for 121895
Made data for 121896
Made data for 121897
Made data for 121898
Made data for 121899
Made data for 121900
Made data for 121901
Made data for 121902
Made data for 121903
Made data for 121904
Made data for 121905
Made data for 121906
Made data for 121907
Made data for 121908
Made data for 121909
Made data for 121910
Made data for 121911
Made data for 121912
Made data for 121913
Made data for 121914
Made data for 121915
Made data for 121916
Made data for 121917
Made data for 121918
Made data for 121919
Made data for 121920
Made data for 121921
Made data for 121922
Made data for

## Concatenate the individual careers 

In [17]:
fs = [f for f in os.listdir(raw) if f.endswith('.txt')]
df = pd.DataFrame()
for i in fs:
    df_add = pd.read_csv(raw+i,header=0)
    
    if i.startswith("/fighter/"): #need this to add the entry to sherdog list of all links scraped
        file_name = i[9:]
    else :
        file_name = i.replace("/","_")

    df_add['name']= file_name
    df = pd.concat([df, df_add], axis=0)
    print("%s added." %(file_name))

1651-1651-40638.txt added.
A-Cenan-8554.txt added.
A-Gunawan-31680.txt added.
A-Hu-63997.txt added.
A-Li-Mu-Jiang-26393.txt added.
A-Parry-15961.txt added.
A-Qiao-95869.txt added.
A-Si-Ri-La-Tu-84013.txt added.
Aabdurazzokkhuzh-Odilkhuzhev-386706.txt added.
Aadam-Grant-249817.txt added.
Aadil-Bashir-116871.txt added.
Aakash-Rana-245063.txt added.
Aalambek-Umarbekov-400727.txt added.
Aalon-Cruz-103485.txt added.
Aarason-Perry-114237.txt added.
Aaron-Abbott-59802.txt added.
Aaron-Aby-84616.txt added.
Aaron-Acero-12109.txt added.
Aaron-Adams-70014.txt added.
Aaron-Adamson-55995.txt added.
Aaron-Aguilera-15745.txt added.
Aaron-Alejandro-Higuera-Villa-317859.txt added.
Aaron-Allison-26287.txt added.
Aaron-Anderson-3529.txt added.
Aaron-Anspach-54221.txt added.
Aaron-Arana-43662.txt added.
Aaron-Armstrong-31019.txt added.
Aaron-Arnsmeyer-5832.txt added.
Aaron-Asada-34887.txt added.
Aaron-Aschendorf-52484.txt added.
Aaron-BadBear-250373.txt added.
Aaron-Barker-76498.txt added.
Aaron-Barnard-2

Aaron-Salisbury-25216.txt added.
Aaron-Sattor-85533.txt added.
Aaron-Sawyer-35046.txt added.
Aaron-Schenk-40452.txt added.
Aaron-Shmyr-74091.txt added.
Aaron-Shultz-27133.txt added.
Aaron-Silvia-23176.txt added.
Aaron-Simpson-24986.txt added.
Aaron-Skates-39676.txt added.
Aaron-Skinner-46394.txt added.
Aaron-Smith-10415.txt added.
Aaron-Smith-147781.txt added.
Aaron-Smith-181777.txt added.
Aaron-Snyder-42626.txt added.
Aaron-Snyder-62780.txt added.
Aaron-Spurge-52788.txt added.
Aaron-St-Louis-25305.txt added.
Aaron-Stagmeir-36061.txt added.
Aaron-Stark-14710.txt added.
Aaron-Steadman-46260.txt added.
Aaron-Steed-2298.txt added.
Aaron-Steele-11746.txt added.
Aaron-Stregles-4333.txt added.
Aaron-Suarez-41017.txt added.
Aaron-Sullivan-14122.txt added.
Aaron-Sunderland-17901.txt added.
Aaron-Sutton-100249.txt added.
Aaron-Sutton-56112.txt added.
Aaron-Swark-52105.txt added.
Aaron-Tau-228831.txt added.
Aaron-Teed-53063.txt added.
Aaron-Thomas-54786.txt added.
Aaron-Thompson-44109.txt added.

Abdul-Bari-147139.txt added.
Abdul-Baybulatov-127163.txt added.
Abdul-Chyasi-217469.txt added.
Abdul-Crabid-52828.txt added.
Abdul-Dalgatov-240407.txt added.
Abdul-Elwahab-Saeed-240609.txt added.
Abdul-Eymatov-379537.txt added.
Abdul-Gaziev-282615.txt added.
Abdul-Hadi-92975.txt added.
Abdul-Hameed-214477.txt added.
Abdul-Hamid-132283.txt added.
Abdul-Hannan-394067.txt added.
Abdul-Hassan-5663.txt added.
Abdul-Hussein-212403.txt added.
Abdul-Ibragimov-86976.txt added.
Abdul-Kader-Souane-186915.txt added.
Abdul-Kamara-161769.txt added.
Abdul-Karim-Badakhshi-304639.txt added.
Abdul-Khaliq-Ghowsi-244041.txt added.
Abdul-Khaliq-Rashid-313631.txt added.
Abdul-Kudbidinov-235959.txt added.
Abdul-Majid-26065.txt added.
Abdul-Malick-Adjei-312863.txt added.
Abdul-Malik-Dzhamalov-311717.txt added.
Abdul-Matin-153267.txt added.
Abdul-Mogomedov-173327.txt added.
Abdul-Mohamed-311645.txt added.
Abdul-Mohamed-8512.txt added.
Abdul-Moqtader-Oryakhil-298615.txt added.
Abdul-Mubeen-283075.txt added.
Abd

Abdurashitov-Deierbek-368049.txt added.
Abdurasul-Koylubay-Uulu-301521.txt added.
Abdurasul-Kuldashev-285311.txt added.
Abdurasul-Sadykov-105533.txt added.
Abdurasul-Ulanbek-265505.txt added.
Abdurasul-uulu-Nursultan-324333.txt added.
Abdurasul-Valiev-346147.txt added.
Abdurauf-Dzhalilov-343205.txt added.
Abdurazak-Mansurov-307407.txt added.
Abdurazak-Turaev-384483.txt added.
Abdurokhman-Garasaev-297239.txt added.
Abdurrahman-Adel-380215.txt added.
Abdurrauf-Abdul-Karim-326007.txt added.
Abdusalam-Sayida-390525.txt added.
Abdusalam-Uulu-Esenbay-209613.txt added.
Abdusalim-Khamitov-381511.txt added.
Abdusalim-Sharipov-381295.txt added.
Abdusalom-Niyazov-381327.txt added.
Abdusalom-Shamsov-355011.txt added.
Abdusamad-Kirgizov-247233.txt added.
Abdusamad-Rakhmatov-364457.txt added.
Abdusamad-Sangov-221833.txt added.
Abdushakhboz-Mirzoev-284411.txt added.
Abdusharif-Khomidov-162273.txt added.
Abdussamat-Tezekov-298151.txt added.
Abduvali-Uulu-Nurgeldi-360657.txt added.
Abduvayit-Osmonali-2

Abylkasym-Yakubov-204201.txt added.
Abyt-Nurmanov-349707.txt added.
Abzal-Aziz-360425.txt added.
Abzal-Seitjapparov-377573.txt added.
AC-Gamez-1016.txt added.
Acacio-dos-Santos-127365.txt added.
Acacio-Gomes-de-Melo-264865.txt added.
Acacio-Pereira-Amorim-176893.txt added.
Acacio-Silas-Vicente-dos-Santos-239069.txt added.
Ace-Anderson-15003.txt added.
Ace-Anuera-304365.txt added.
Ace-Arsov-252879.txt added.
Ace-Lewis-77210.txt added.
Acelino-Lima-21016.txt added.
Aceng-Adih-323575.txt added.
Achala-Bopitiya-91019.txt added.
Achille-Bokononhui-312835.txt added.
Achille-Moretto-129359.txt added.
Achilleas-Chalkidis-118171.txt added.
Achilles-Estremadura-68610.txt added.
Achilles-Wash-14326.txt added.
Achim-Lausecker-8572.txt added.
Achmad-Daryani-31443.txt added.
Achmad-Eko-Priandono-295785.txt added.
Achmad-Fauzi-31684.txt added.
Achmad-Muhaimin-299115.txt added.
Achmadi-Achmadi-302555.txt added.
Achmed-Dashajev-52229.txt added.
Achmed-Labasanov-1437.txt added.
Achmed-Wagabov-22264.txt 

...

Yuto-Goto-113615.txt added.
Yuto-Hirose-402100.txt added.
Yuto-Hiyama-86603.txt added.
Yuto-Hokamura-80347.txt added.
Yuto-Inoue-276897.txt added.
Yuto-Kaneki-89199.txt added.
Yuto-Kimura-294871.txt added.
Yuto-Nakajima-79542.txt added.
Yuto-Nakamori-224289.txt added.
Yuto-Sekiguchi-128935.txt added.
Yuto-Shimoda-129449.txt added.
Yuto-Uda-321191.txt added.
Yuto-Yamaura-110859.txt added.
Yutoku-Umeki-381201.txt added.
Yuuki-Kondo-5107.txt added.
Yuuki-Yuuki-255421.txt added.
Yuvoke-Collins-397912.txt added.
Yuya-Aikawa-24393.txt added.
Yuya-Hayashi-157915.txt added.
Yuya-Ito-44256.txt added.
Yuya-Kaneuchi-15480.txt added.
Yuya-Kashiwagi-172899.txt added.
Yuya-Kato-390919.txt added.
Yuya-Kawabe-205841.txt added.
Yuya-Kimura-388424.txt added.
Yuya-Kodama-116729.txt added.
Yuya-Matsuno-186151.txt added.
Yuya-Nabekubo-386494.txt added.
Yuya-Nagai-54944.txt added.
Yuya-Ono-40643.txt added.
Yuya-Onodera-61071.txt added.
Yuya-Osugi-20008.txt added.
Yuya-Sakanishi-84401.txt added.
Yuya-Seino-7

Zack-Ilarraza-34183.txt added.
Zack-Jones-49147.txt added.
Zack-Konkel-34770.txt added.
Zack-Legner-18043.txt added.
Zack-Mahar-41093.txt added.
Zack-Mathews-35647.txt added.
Zack-Mathiew-233309.txt added.
Zack-McCone-229469.txt added.
Zack-Meadows-51809.txt added.
Zack-Phennacie-3444.txt added.
Zack-Potter-29210.txt added.
Zack-Quinlan-134873.txt added.
Zack-Rapal-30056.txt added.
Zack-Schroeder-12128.txt added.
Zack-Shaw-243989.txt added.
Zack-Shelley-22863.txt added.
Zack-Stansworth-37106.txt added.
Zack-Surdyka-33293.txt added.
Zack-Trammel-28247.txt added.
Zack-Wakeman-25080.txt added.
Zack-Welker-1904.txt added.
Zack-Wells-230089.txt added.
Zack-Wilson-46833.txt added.
Zack-Wiph-63004.txt added.
Zack-Yngojo-21891.txt added.
Zackaria-Badji-171455.txt added.
Zackaria-Guezzar-174525.txt added.
Zackery-Burns-58341.txt added.
Zackery-Powell-299667.txt added.
Zad-Mangat-219755.txt added.
Zadeh-Hossein-382383.txt added.
Zadie-Morris-36314.txt added.
Zaeem-Yakub-10553.txt added.
Zaenudin

Zaur-Tarikuliev-264559.txt added.
Zaur-Zhantegolov-165725.txt added.
Zaurbek-Abdurakhmanov-375484.txt added.
Zaurbek-Asuev-263363.txt added.
Zaurbek-Aysinov-301545.txt added.
Zaurbek-Bashaev-189177.txt added.
Zaurbek-Darsigov-233599.txt added.
Zaurbek-Dryaev-174221.txt added.
Zaurbek-Ibragimov-100833.txt added.
Zaurbek-Khidrimov-367971.txt added.
Zaurbek-Kosulov-173185.txt added.
Zaurbek-Muchaev-37417.txt added.
Zaurbek-Navrazov-282079.txt added.
Zaurbek-Pliev-244753.txt added.
Zaurbek-Tedeev-146611.txt added.
Zaurbek-Yusupov-254095.txt added.
Zauri-Maisuradze-101359.txt added.
Zavier-Garcia-84122.txt added.
Zavkivbek-Mirov-381322.txt added.
Zavlonbek-Ostonov-335767.txt added.
Zavohir-Karimzhanuly-335061.txt added.
Zavudin-Edelkhadjaev-214457.txt added.
Zavur-Abdulayev-380801.txt added.
Zaxton-Kamaka-259591.txt added.
Zaydula-Uulu-Seyit-330265.txt added.
Zaynal-Osmanov-375867.txt added.
Zaynilobidin-Latipov-346897.txt added.
Zaynudin-Suleymanov-347725.txt added.
Zaynulabid-Zaynulabidov

Zharkov-Igor-28813.txt added.
Zharkyn-Baizakov-82152.txt added.
Zharkynbay-Zamirbek-uulu-398840.txt added.
Zhasulan-Adibaev-316315.txt added.
Zhasulan-Akimzhanov-221983.txt added.
Zhasulan-Dauletkaliev-245011.txt added.
Zhasulan-Karakulov-236679.txt added.
Zhasulan-Khasimov-175889.txt added.
Zhasur-Abdimurodov-366951.txt added.
Zhasur-Anarbaev-245005.txt added.
Zhasur-Mirzavaliev-392822.txt added.
Zhasur-Nafasov-375524.txt added.
Zhasur-Rasametov-237465.txt added.
Zhasur-Tolkumov-394368.txt added.
Zhasur-Usupov-330119.txt added.
Zhasura-Rakimov-390538.txt added.
Zhasurbek-Anarboev-284501.txt added.
Zhasurbek-Komilov-297503.txt added.
Zhasurbek-Norov-346139.txt added.
Zhasurbek-Numonzhon-Ogliy-Sotvoldiev-342955.txt added.
Zhasurbek-Sobirov-377824.txt added.
Zhasurbek-Tumanov-383700.txt added.
Zhasurbek-Zholdoshev-322641.txt added.
Zhavakhir-Khayrullaev-403421.txt added.
Zhavakr-Panjiev-385183.txt added.
Zhavlon-Khasanov-316111.txt added.
Zhavlonbek-Odilov-377881.txt added.
Zhavokhir-Mir

Zoltan-Turai-128197.txt added.
Zolto-Tsibenov-337671.txt added.
Zonunthara-Tlau-286097.txt added.
Zoran-Bozovic-117359.txt added.
Zoran-Bubalo-237211.txt added.
Zoran-Cingelic-244993.txt added.
Zoran-Dod-101859.txt added.
Zoran-Galic-26963.txt added.
Zoran-Grgic-4705.txt added.
Zoran-Krpan-102109.txt added.
Zoran-Milacic-87184.txt added.
Zoran-Milic-281187.txt added.
Zoran-Milovic-101685.txt added.
Zoran-Mladenovic-82117.txt added.
Zoran-Petkovic-282527.txt added.
Zoran-Saric-40563.txt added.
Zoran-Solaja-279351.txt added.
Zoran-Spasojevic-229287.txt added.
Zoran-Vitanov-96429.txt added.
Zoran-Ziza-56363.txt added.
Zoren-Pescador-118555.txt added.
Zorigto-Mizhidon-274793.txt added.
Zorigto-Shubin-244091.txt added.
Zorikto-Galsanov-237921.txt added.
Zorislav-Kainskiy-145087.txt added.
Zorka-Stojanovic-249203.txt added.
Zorobabel-Moreira-41618.txt added.
Zouhere-el-Assadi-41867.txt added.
Zouhir-BadreEddine-160759.txt added.
Zouhir-Boumenir-59862.txt added.
Zouhir-Mallem-266421.txt added

In [18]:
df.to_csv(path+r'sherdog_sample.csv', index = False)